In [5]:
# Téléchargement des librairies *
import requests
import lxml.html

In [15]:
url = "https://codes.droit.org/"

r = requests.get(url)
r.status_code # test url status code = 200 OK !

200

In [7]:
root = lxml.html.fromstring(r.content)

balises_liens = root.xpath('//dd/a[3]') # trouver les balises contenant les liens
# la troisième a car les deux premières contiennent les liens pdf et rss

#/html/body/article/dl[4]/dd
#/html/body/article/dl[4]/dd/a[3]
print(balises_liens) # imprimer les balises contenant les liens

[<Element a at 0x7e8e830f2a30>, <Element a at 0x7e8e70bd6bc0>, <Element a at 0x7e8e70bd6c60>, <Element a at 0x7e8e70bd6c10>, <Element a at 0x7e8e70bd6cb0>, <Element a at 0x7e8e70bd6d00>, <Element a at 0x7e8e70bd6d50>, <Element a at 0x7e8e70bd6da0>, <Element a at 0x7e8e70bd6df0>, <Element a at 0x7e8e70bd6e40>, <Element a at 0x7e8e70bd6e90>, <Element a at 0x7e8e70bd6ee0>, <Element a at 0x7e8e70bd6f30>, <Element a at 0x7e8e70bd6f80>, <Element a at 0x7e8e70bd6fd0>, <Element a at 0x7e8e70bd7020>, <Element a at 0x7e8e70bd7070>, <Element a at 0x7e8e70bd70c0>, <Element a at 0x7e8e70bd7110>, <Element a at 0x7e8e70bd7160>, <Element a at 0x7e8e70bd71b0>, <Element a at 0x7e8e70bd7200>, <Element a at 0x7e8e70bd7250>, <Element a at 0x7e8e70bd72a0>, <Element a at 0x7e8e70bd72f0>, <Element a at 0x7e8e70bd7340>, <Element a at 0x7e8e70bd7390>, <Element a at 0x7e8e70bd73e0>, <Element a at 0x7e8e70bd7430>, <Element a at 0x7e8e70bd7480>, <Element a at 0x7e8e70bd74d0>, <Element a at 0x7e8e70bd7520>, <Elemen

In [12]:
url_list = []

for element in balises_liens:
    href = element.attrib['href']
    if href.startswith('http://') or href.startswith('https://'): 
        # vérifie que les liens appartiennent au même site 
        # url_list.append(href)
        pass
    elif href.startswith('/'):
        url_list.append('https://codes.droit.org/' + href)
    else:
        url_list.append('https://codes.droit.org/' + href)
    
print(url_list)

['https://codes.droit.org/payloads/Code%20de%20l%27action%20sociale%20et%20des%20familles.xml', 'https://codes.droit.org/payloads/Code%20de%20l%27artisanat.xml', 'https://codes.droit.org/payloads/Code%20des%20assurances.xml', 'https://codes.droit.org/payloads/Code%20de%20l%27aviation%20civile.xml', 'https://codes.droit.org/payloads/Code%20du%20cin%C3%A9ma%20et%20de%20l%27image%20anim%C3%A9e.xml', 'https://codes.droit.org/payloads/Code%20civil.xml', 'https://codes.droit.org/payloads/Code%20de%20la%20commande%20publique.xml', 'https://codes.droit.org/payloads/Code%20de%20commerce.xml', 'https://codes.droit.org/payloads/Code%20des%20communes.xml', 'https://codes.droit.org/payloads/Code%20des%20communes%20de%20la%20Nouvelle-Cal%C3%A9donie.xml', 'https://codes.droit.org/payloads/Code%20de%20la%20consommation.xml', 'https://codes.droit.org/payloads/Code%20de%20la%20construction%20et%20de%20l%27habitation.xml', 'https://codes.droit.org/payloads/Code%20de%20la%20d%C3%A9fense.xml', 'https://cod

In [2]:
# TEST avec 1 code de loi 
url_list = ['https://codes.droit.org/payloads/Code%20de%20l%27action%20sociale%20et%20des%20familles.xml']
print(url_list)

['https://codes.droit.org/payloads/Code%20de%20l%27action%20sociale%20et%20des%20familles.xml']


In [23]:
from collections import namedtuple
from bs4 import BeautifulSoup

Loi = namedtuple('Loi', ['num', 'title', 'id', 'date', 'body'])
# mettre toutes les infos dans l'objet loi 
liste_lois = []

for url in url_list:
    req = requests.get(url)
    code_texte = req.text
    code_soup = BeautifulSoup(code_texte, 'xml')
    
    nom_code = code_soup.code['nom']

    for article in code_soup.find_all('article'): 
        l_num = article['num']
        num = f""
        title = f"{l_num} du {nom_code}"
        id = article['id']
        date = article['date']
        body = article.text
        
        loi = Loi(num, title, id, date, body)
        liste_lois.append(loi)

print(liste_lois)



[Loi(num='', title="L111-1 du Code de l'action sociale et des familles", id='LEGIARTI000006796412', date='2002-01-03', body="\n\nSous réserve des dispositions des articles L. 111-2 et L. 111-3, toute personne résidant en France bénéficie, si elle remplit les conditions légales d'attribution, des formes de l'aide sociale telles qu'elles sont définies par le présent code.\n"), Loi(num='', title="L111-2 du Code de l'action sociale et des familles", id='LEGIARTI000030957743', date='2015-07-30', body="\nLes personnes de nationalité étrangère bénéficient dans les conditions propres à chacune de ces prestations : \n1° Des prestations d'aide sociale à l'enfance ; \n2° De l'aide sociale en cas d'admission dans un centre d'hébergement et de réinsertion sociale ; \n3° De l'aide médicale de l'Etat ; \n4° Des allocations aux personnes âgées prévues à l'article L. 231-1 à condition qu'elles justifient d'une résidence ininterrompue en France métropolitaine depuis au moins quinze ans avant soixante-di

In [24]:
import csv

with open('./data/test1.csv', 'w') as f:
    writer = csv.writer(f)
    writer.writerow(Loi._fields)
    for loi in liste_lois:
        writer.writerow(loi)